In [3]:
import numpy as np
import polars as pl
import os

import cmdstanpy
import arviz as az

import iqplot
import bebi103

import bokeh.io
from bokeh.models import Legend
bokeh.io.output_notebook()

Loading BokehJS ...

In [ ]:
# Load data set
# df = pl.read_csv("data/gardner_mt_catastrophe_only_tubulin.csv", skip_rows=9)
df_12 = df.select(pl.col('12 uM'))

a) Describe the first three models as stories. Give physical descriptions of the meanings of their parameters. <br> 
 Describe how these models are related to each other. <br>
 Recall that we worked out the likelihood for model 4 in a previous exercise. <br> 
 How is it related to the other three models?

Model 1: Exponential distribution with a single rate parameter (β). <br> 
- Microtubule catastrophe occurs as a single, random "failure" event. <br>
- The rate parameter is the average rate of catastrophe
- The physical meaning is that the microtuble has no memory and doesn't get more risky over time.

Model 2: Gamma distribution with two parameters α and β. <br>
- Microtubule catastrophe requires the accumulation of multiple events before catastrophe occurs. <br>
- α is the shape parameter - The number of Possion prcosses arrivals before catstrophe event <br>
- β rate parameter - The rate at which each damage event occurs <br>
- The physical meaning is that if α > 1 a catastrophe event is unlickely at a given initial period where the microtubule is "safe" 

Model 3: Weibull Distribution with two parameters α and σ <br>
- The posibility for a catastrophe changes over time, this models a wear-out process of the microtubule <br>
- α is the shape parameter - dictate the shape of the curves, basically determines how the microtubule acts over time <br>
    when α < 1 it becomes more stable, α = 1 is the same as exponential and when α > 1 it becomes less stable over time <br>
- σ is the scale parameter - dicatates the rate of arrivals
- The physical meaning is that microtubule catastrophe becomes more and more likely as the it grows 

Model 4 has two events exponential distibuted with different rates(β1 and β2) <br>
- It is related to model 2 becuase when β1 = β2 they are the same and it becomes Gamma(α=2, β=2β) distribution <br>
- In case one of the rates dominates the other β1 >> β2 The distribution will approach Exponential(β₂) distribution <br>
- When α = 1 Weibull becomes an exponential distribution 

b) Build full Bayesian generative models for each of the models. Be sure to perform prior predictive checks. <br>
After building the model, perform parameter estimates, and then do posterior predictive checks.

In [5]:
rng = np.random.default_rng()
n_samples = 100   # samples per curve
n_curves = 100    # number of prior predictive draws

def plot_model(samples_list, title):
    data = []
    labels = []
    for i, s in enumerate(samples_list):
        data.extend(s)
        labels.extend([f"draw {i}"] * len(s))

    df = pl.DataFrame({"time": data, "draw": labels})
    
    p = iqplot.ecdf(
        df,
        q="time",
        cats="draw",
        marker_kwargs={"alpha": 0.15, "color": "steelblue"},
        line_kwargs={"alpha": 0.15, "color": "steelblue"},
        x_axis_type='log'
    )
    p.title.text = title
    p.xaxis.axis_label = "Time to catastrophe (s)"
    p.yaxis.axis_label = "ECDF"
    
    p.legend.visible = False
    return p

Model 1 - Exponential distribution with a single rate parameter (β)

In [13]:
exp_curves = []

for _ in range(n_curves):
        beta_1 = np.abs(rng.normal(0, 0.5))
        exp_curves.append(rng.exponential(1/beta_1, n_samples))

p1 = plot_model(exp_curves, "Model 1: Exponential")


bokeh.io.show(p1)

Model 2: Gamma distribution with two parameters α and β

In [28]:
gamma_curves = []

for _ in range(n_curves):
    alpha_2 = rng.lognormal(mean=1, sigma=0.5)  
    beta_2  = rng.lognormal(mean=0.0, sigma=0.5)  
    gamma_curves.append(rng.gamma(alpha_2, 1/beta_2, n_samples))

p2 = plot_model(gamma_curves, "Model 2: Gamma")

bokeh.io.show(p2)


Model 3: Weibull Distribution with two parameters α and σ

In [33]:
weibull_curves = []

for _ in range(n_curves):
    alpha_3 = rng.lognormal(mean=5, sigma=1, size=n_samples)
    sigma_3 = rng.lognormal(mean=2, sigma=1, size=n_samples)
    weibull_curves.append(sigma_3 * rng.weibull(alpha_3, n_samples))

p3 = plot_model(weibull_curves, "Model 3: Weibull")

bokeh.io.show(p3)

Model 4 has two events exponential distibuted with different rates(β1 and β2)

In [8]:
hypo_curves = []

for _ in range(n_curves):
    beta_4_1 = np.abs(rng.normal(loc=0, scale=1.0)) 
    beta_4_2 = np.abs(rng.normal(loc=0, scale=1.0))
    x1 = rng.exponential(1/beta_4_1, n_samples)
    x2 = rng.exponential(1/beta_4_2, n_samples)
    hypo_curves.append(x1 + x2)

p4 = plot_model(hypo_curves, "Model 4: Hypoexponential")
# p4 = iqplot.ecdf(df_12, q="12 uM", line_kwargs={"line_width":1, "color":"red"}, p=p4)
bokeh.io.show(p4)

## Start sampling different models:

In [14]:
data_12 = df_12.drop_nulls().to_numpy().flatten()

stan_data = {
    'n': len(data_12),
    'y': data_12
}

### Exponential distribution sampling:

In [15]:
sm_exponential = cmdstanpy.CmdStanModel(stan_file='stan_files/microtubule_catastrophe_exponential.stan')
samples_exponential = az.from_cmdstanpy(sm_exponential.sample(data=stan_data, chains=4, iter_warmup=1000, iter_sampling=2000),
                                        posterior_predictive='y_rep')

19:43:40 - cmdstanpy - INFO - compiling stan file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_exponential.stan to exe file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_exponential
19:43:54 - cmdstanpy - INFO - compiled model executable: /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_exponential
19:43:54 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

19:43:58 - cmdstanpy - INFO - CmdStan done processing.
19:43:58 - cmdstanpy - WARNING - Non-fatal error during sampling:
Exception: exponential_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_exponential.stan', line 12, column 4 to column 26)
	Exception: exponential_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_exponential.stan', line 12, column 4 to column 26)
	Exception: exponential_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_exponential.stan', line 12, column 4 to column 26)
	Exception: exponential_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_exponential.stan', line 12, column 4 to column 26)
	Exception: exponential_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_exponential.stan', line 12, column 4 to column 26)
	Exception: exponential_lpdf: Inver

In [16]:
bokeh.io.show(
    bebi103.viz.corner(
        samples_exponential, 
        parameters=[('beta', 'β')], 
        # plot_ecdf=True,
    )
)

In [18]:
p = None
y_rep = samples_exponential.posterior_predictive['y_rep'].stack({'sample': ('chain', 'draw')}).transpose('sample', 'y_rep_dim_0').values

p = bebi103.viz.predictive_ecdf(y_rep, p=p, data = data_12, diff='ecdf')

bokeh.io.show(p)

In [19]:
weic_exponential = az.waic(samples_exponential, scale="deviance")
loo_exponential = az.loo(samples_exponential, scale="deviance")

print(weic_exponential)
print(loo_exponential)

Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

              Estimate       SE
deviance_waic  9608.58    32.04
p_waic            0.37        -
Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

             Estimate       SE
deviance_loo  9608.58    32.04
p_loo            0.37        -
------

Pareto k diagnostic values:
                         Count   Pct.
(-Inf, 0.70]   (good)      692  100.0%
   (0.70, 1]   (bad)         0    0.0%
   (1, Inf)   (very bad)    0    0.0%



### Gamma distribution sampling:

In [29]:
# Model 2: Gamma distribution
sm_gamma = cmdstanpy.CmdStanModel(stan_file='stan_files/microtubule_catastrophe_gamma.stan')
samples_gamma = az.from_cmdstanpy(sm_gamma.sample(data=stan_data, chains=4, iter_warmup=1000, iter_sampling=2000),
                                  posterior_predictive='y_rep')


19:59:25 - cmdstanpy - INFO - compiling stan file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_gamma.stan to exe file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_gamma
19:59:38 - cmdstanpy - INFO - compiled model executable: /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_gamma
19:59:38 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

19:59:43 - cmdstanpy - INFO - CmdStan done processing.
19:59:43 - cmdstanpy - WARNING - Non-fatal error during sampling:
Exception: gamma_lpdf: Shape parameter is inf, but must be positive finite! (in 'microtubule_catastrophe_gamma.stan', line 15, column 4 to column 27)
	Exception: gamma_lpdf: Shape parameter is inf, but must be positive finite! (in 'microtubule_catastrophe_gamma.stan', line 15, column 4 to column 27)
	Exception: gamma_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_gamma.stan', line 15, column 4 to column 27)
	Exception: gamma_lpdf: Inverse scale parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_gamma.stan', line 15, column 4 to column 27)
	Exception: gamma_lpdf: Shape parameter is inf, but must be positive finite! (in 'microtubule_catastrophe_gamma.stan', line 15, column 4 to column 27)
	Exception: gamma_lpdf: Shape parameter is inf, but must be positive finite! (in 'microtubule_catastrophe_gamma.s

In [30]:
bokeh.io.show(
    bebi103.viz.corner(
        samples_gamma, 
        parameters=['alpha', 'beta'], 
        # plot_ecdf=True,
    )
)

In [31]:
p = None
y_rep = samples_gamma.posterior_predictive['y_rep'].stack({'sample': ('chain', 'draw')}).transpose('sample', 'y_rep_dim_0').values

p = bebi103.viz.predictive_ecdf(y_rep, p=p, data = data_12, diff='ecdf')

bokeh.io.show(p)

In [32]:
weic_gamma = az.waic(samples_gamma, scale="deviance")
loo_gamma = az.loo(samples_gamma, scale="deviance")

print(weic_gamma)
print(loo_gamma)

Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

              Estimate       SE
deviance_waic  9279.61    47.52
p_waic            2.32        -
Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

             Estimate       SE
deviance_loo  9279.61    47.52
p_loo            2.32        -
------

Pareto k diagnostic values:
                         Count   Pct.
(-Inf, 0.70]   (good)      692  100.0%
   (0.70, 1]   (bad)         0    0.0%
   (1, Inf)   (very bad)    0    0.0%



### Weibull distribution sampling:

In [34]:
# Model 3: Weibull distribution
sm_weibull = cmdstanpy.CmdStanModel(stan_file='stan_files/microtubule_catastrophe_weibull.stan')
samples_weibull = az.from_cmdstanpy(sm_weibull.sample(data=stan_data, chains=4, iter_warmup=1000, iter_sampling=2000),
                                  posterior_predictive='y_rep')


20:14:14 - cmdstanpy - INFO - compiling stan file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_weibull.stan to exe file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_weibull
20:14:33 - cmdstanpy - INFO - compiled model executable: /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_weibull
20:14:33 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

20:14:39 - cmdstanpy - INFO - CmdStan done processing.
20:14:39 - cmdstanpy - WARNING - Non-fatal error during sampling:
Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.stan', line 14, column 4 to column 30)
	Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.stan', line 14, column 4 to column 30)
	Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.stan', line 14, column 4 to column 30)
	Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.stan', line 14, column 4 to column 30)
	Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.stan', line 14, column 4 to column 30)
Exception: weibull_lpdf: Shape parameter is 0, but must be positive finite! (in 'microtubule_catastrophe_weibull.st

In [35]:
bokeh.io.show(
    bebi103.viz.corner(
        samples_weibull, 
        parameters=['alpha', 'sigma'], 
        # plot_ecdf=True,
    )
)

In [36]:
p = None
y_rep = samples_weibull.posterior_predictive['y_rep'].stack({'sample': ('chain', 'draw')}).transpose('sample', 'y_rep_dim_0').values

p = bebi103.viz.predictive_ecdf(y_rep, p=p, data = data_12, diff='ecdf')

bokeh.io.show(p)

In [37]:
waic_weibull = az.waic(samples_weibull, scale="deviance")
loo_weibull = az.loo(samples_weibull, scale="deviance")

print(waic_weibull)
print(loo_weibull)

/root/projects/wis-stats/.pixi/envs/default/lib/python3.13/site-packages/arviz/stats/stats.py:1667: UserWarning: For one or more samples the posterior variance of the log predictive densities exceeds 0.4. This could be indication of WAIC starting to fail. 
See http://arxiv.org/abs/1507.04544 for details
  warnings.warn(


Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

              Estimate       SE
deviance_waic  9314.04    48.58
p_waic            2.97        -

There has been a warning during the calculation. Please check the results.
Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

             Estimate       SE
deviance_loo  9314.05    48.58
p_loo            2.97        -
------

Pareto k diagnostic values:
                         Count   Pct.
(-Inf, 0.70]   (good)      692  100.0%
   (0.70, 1]   (bad)         0    0.0%
   (1, Inf)   (very bad)    0    0.0%



### Hypoexponential distribution with 2 rates sampling:

In [38]:
data_12 = df_12.drop_nulls().to_numpy().flatten()

stan_data_hypo = {'N': len(data_12),""
                    'y': data_12}

In [39]:
# Model 4: hypo distribution
sm_hypo = cmdstanpy.CmdStanModel(stan_file='stan_files/microtubule_catastrophe_hypo_2.stan')
samples_hypo = az.from_cmdstanpy(sm_hypo.sample(data=stan_data_hypo, chains=4, iter_warmup=1000, iter_sampling=2000),
                                  posterior_predictive='y_rep')


20:45:57 - cmdstanpy - INFO - compiling stan file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_hypo_2.stan to exe file /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_hypo_2
20:46:15 - cmdstanpy - INFO - compiled model executable: /root/projects/wis-stats/submission/stan_files/microtubule_catastrophe_hypo_2
20:46:15 - cmdstanpy - INFO - CmdStan start processing


chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

20:46:22 - cmdstanpy - INFO - CmdStan done processing.


In [40]:
bokeh.io.show(
    bebi103.viz.corner(
        samples_hypo, 
        parameters=['beta_1', 'beta_2'], 
        # plot_ecdf=True,
    )
)

In [41]:
p = None
y_rep = samples_hypo.posterior_predictive['y_rep'].stack({'sample': ('chain', 'draw')}).transpose('sample', 'y_rep_dim_0').values

p = bebi103.viz.predictive_ecdf(y_rep, p=p, data = data_12, diff='ecdf')

bokeh.io.show(p)

In [42]:
waic_hypo = az.waic(samples_hypo, scale="deviance")
loo_hypo = az.loo(samples_hypo, scale="deviance")

print(waic_hypo)
print(loo_hypo) 

Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

              Estimate       SE
deviance_waic  9326.12    36.82
p_waic            0.76        -
Computed from 8000 posterior samples and 692 observations log-likelihood matrix.

             Estimate       SE
deviance_loo  9326.12    36.82
p_loo            0.76        -
------

Pareto k diagnostic values:
                         Count   Pct.
(-Inf, 0.70]   (good)      692  100.0%
   (0.70, 1]   (bad)         0    0.0%
   (1, Inf)   (very bad)    0    0.0%



In [43]:
az.compare({"expo":samples_exponential ,"gamma": samples_gamma,"weibull": samples_weibull, "hypo": samples_hypo}, ic="loo", scale="deviance")

rank     elpd_loo     p_loo   elpd_diff        weight         se  \
gamma       0  9279.611918  2.320950    0.000000  8.582156e-01  47.522403   
weibull     1  9314.047454  2.970906   34.435536  1.584999e-12  48.582823   
hypo        2  9326.123448  0.762202   46.511530  1.417844e-01  36.818254   
expo        3  9608.580190  0.369103  328.968272  1.059153e-13  32.039724   

               dse  warning     scale  
gamma     0.000000    False  deviance  
weibull  10.300165    False  deviance  
hypo     15.898524    False  deviance  
expo     30.354699    False  deviance

Comparing all four models, the gamme model has the best performance, with the highest weight and relatively low complexity.